In [2]:
import pandas as pd
import numpy as np
from datetime import datetime
from sklearn.preprocessing import StandardScaler
import lightgbm as lgb
import xgboost as xgb
from sklearn.model_selection import KFold
from sklearn.ensemble import RandomForestRegressor
from sklearn.multioutput import MultiOutputRegressor
from sklearn.metrics import mean_absolute_error
import warnings
from sklearn.preprocessing import StandardScaler
warnings.filterwarnings("ignore")


SEED = 42
n_splits = 8
number = 5000
early_stopping_rounds = 100

In [35]:
train_df = pd.read_csv("train.csv")
test_df = pd.read_csv("test.csv")
eq_df = pd.read_csv("eq.csv")
sample_submission = pd.read_csv("sample_submission.csv")



# test_df.describe()
# test_df.describe()
# test_df.info()
train_df.info()
train_df = train_df.drop(columns=["Unnamed: 0"])
print(f"Training data shape: {train_df.shape}")
print(f"Earthquake data shape: {eq_df.shape}")
print(f"Test data shape: {test_df.shape}")

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1250 entries, 0 to 1249
Data columns (total 21 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   Unnamed: 0  1250 non-null   int64  
 1   year        1250 non-null   int64  
 2   month       1250 non-null   int64  
 3   day         1250 non-null   int64  
 4   hour        1250 non-null   int64  
 5   min         1250 non-null   int64  
 6   sec         1250 non-null   int64  
 7   lat         1250 non-null   float64
 8   lon         1250 non-null   float64
 9   depth       1250 non-null   int64  
 10  class       1250 non-null   float64
 11  year_as     1250 non-null   int64  
 12  month_as    1250 non-null   int64  
 13  day_as      1250 non-null   int64  
 14  hour_as     1250 non-null   int64  
 15  min_as      1250 non-null   int64  
 16  sec_as      1250 non-null   int64  
 17  lat_as      1250 non-null   float64
 18  lon_as      1250 non-null   float64
 19  depth_as    1250 non-null  

In [36]:
target_cols = ["year_as", "month_as", "day_as", "hour_as", "min_as", "sec_as",
                  "lat_as", "lon_as", "depth_as", "class_as"]

X = train_df.drop(columns=target_cols)
y = train_df[target_cols]

X_test = test_df[X.columns].copy()

In [ ]:
# def earthquake_features_simple(train_path, test_path, create_submission=False):
#     """
#     Simplified preprocessing for earthquake aftershock prediction.
#     Skips datetime processing but keeps essential features.
#     """
#     import pandas as pd
#     import numpy as np
#     from sklearn.preprocessing import StandardScaler
    
#     # Load data
#     train = pd.read_csv(train_path)
#     test = pd.read_csv(test_path)
    
#     # Create target variables for training data (direct component differences)
#     if 'lat_as' in train.columns:
#         # Spatial differences
#         train['lat_diff'] = train['lat_as'] - train['lat']
#         train['lon_diff'] = train['lon_as'] - train['lon']
#         train['depth_diff'] = train['depth_as'] - train['depth']
#         train['class_diff'] = train['class_as'] - train['class']
        
#         # Time differences in components (more reliable than datetime conversion)
#         train['year_diff'] = train['year_as'] - train['year']
#         train['month_diff'] = train['month_as'] - train['month']
#         train['day_diff'] = train['day_as'] - train['day']
#         train['hour_diff'] = train['hour_as'] - train['hour']
#         train['min_diff'] = train['min_as'] - train['min']
#         train['sec_diff'] = train['sec_as'] - train['sec']
        
#         # Approximate time difference in seconds (for modeling purposes)
#         train['time_diff_seconds'] = (
#             train['year_diff'] * 365.25 * 24 * 3600 +
#             train['month_diff'] * 30.44 * 24 * 3600 +
#             train['day_diff'] * 24 * 3600 +
#             train['hour_diff'] * 3600 +
#             train['min_diff'] * 60 +
#             train['sec_diff']
#         )
        
#     # Key spatial features
#     for df in [train, test]:
#         # Region bins
#         df['lat_bin'] = pd.cut(df['lat'], bins=5, labels=False)
#         df['lon_bin'] = pd.cut(df['lon'], bins=5, labels=False)
#         df['depth_bin'] = pd.cut(df['depth'], bins=5, labels=False)
#         df['class_bin'] = pd.cut(df['class'], bins=5, labels=False)
        
#         # Distance from equator and prime meridian
#         df['dist_from_equator'] = abs(df['lat'])
#         df['dist_from_meridian'] = abs(df['lon'])
        
#         # Log transforms and interactions
#         df['depth'] = df['depth'].clip(lower=0)
#         df['class'] = df['class'].clip(lower=0)

#         df['log_depth'] = np.log1p(df['depth'])
#         df['log_class'] = np.log1p(df['class'])
#         df['depth_class_product'] = df['depth'] * df['class']
        
#         # Squared terms
#         df['depth_squared'] = df['depth'] ** 2
#         df['class_squared'] = df['class'] ** 2
        
#         # Simple categoricals
#         df['is_shallow'] = (df['depth'] < 70).astype(int)
#         df['is_deep'] = (df['depth'] > 300).astype(int)
#         df['is_high_energy'] = (df['class'] > df['class'].quantile(0.75)).astype(int)
        
#         # Time features directly from components (no datetime needed)
#         df['is_winter'] = ((df['month'] == 12) | (df['month'] == 1) | (df['month'] == 2)).astype(int)
#         df['is_summer'] = ((df['month'] >= 6) & (df['month'] <= 8)).astype(int)
#         df['is_daytime'] = ((df['hour'] >= 6) & (df['hour'] <= 18)).astype(int)
    
#     # Statistical aggregations by region (critical for good performance)
#     if 'lat_diff' in train.columns:
#         # Create aggregations by lat_bin
#         agg_features = train.groupby('lat_bin').agg({
#             'time_diff_seconds': ['mean', 'median'],
#             'lat_diff': ['mean', 'median'],
#             'lon_diff': ['mean', 'median'],
#             'depth_diff': ['mean', 'median'],
#             'class_diff': ['mean', 'median'],
#         }).reset_index()
        
#         # Flatten column names
#         agg_features.columns = ['lat_bin'] + [f'{col[0]}_{col[1]}_by_lat_bin' 
#                                              for col in agg_features.columns[1:]]
        
#         # Merge with train and test
#         train = train.merge(agg_features, on='lat_bin', how='left')
#         test = test.merge(agg_features, on='lat_bin', how='left')
        
#         # Similar aggregations for lon_bin
#         agg_features = train.groupby('lon_bin').agg({
#             'time_diff_seconds': ['mean', 'median'],
#             'lat_diff': ['mean', 'median'],
#             'lon_diff': ['mean', 'median'],
#             'depth_diff': ['mean', 'median'],
#             'class_diff': ['mean', 'median'],
#         }).reset_index()
        
#         agg_features.columns = ['lon_bin'] + [f'{col[0]}_{col[1]}_by_lon_bin' 
#                                              for col in agg_features.columns[1:]]
        
#         train = train.merge(agg_features, on='lon_bin', how='left')
#         test = test.merge(agg_features, on='lon_bin', how='left')
    
#     # Fill missing values with medians
#     for df in [train, test]:
#         for col in df.columns:
#             if df[col].dtype in ['int64', 'float64'] and df[col].isnull().sum() > 0:
#                 df[col] = df[col].fillna(df[col].median())
    
#     # One-hot encode important categorical features
#     categorical_cols = ['lat_bin', 'lon_bin', 'depth_bin', 'class_bin']
#     train_encoded = pd.get_dummies(train, columns=categorical_cols, drop_first=True)
#     test_encoded = pd.get_dummies(test, columns=categorical_cols, drop_first=True)
    
#     # Ensure test has same columns as train
#     for col in set(train_encoded.columns) - set(test_encoded.columns):
#         test_encoded[col] = 0
    
#     # Prepare feature matrices - exclude unnecessary columns
#     exclude_cols = [
#         'id_eq', 'year', 'month', 'day', 'hour', 'min', 'sec',
#         'year_as', 'month_as', 'day_as', 'hour_as', 'min_as', 'sec_as', 
#         'lat_as', 'lon_as', 'depth_as', 'class_as',
#         'time_diff_seconds', 'lat_diff', 'lon_diff', 'depth_diff', 'class_diff',
#         'year_diff', 'month_diff', 'day_diff', 'hour_diff', 'min_diff', 'sec_diff'
#     ]
    
#     feature_cols = [c for c in train_encoded.columns if c not in exclude_cols]
    
#     X_train = train_encoded[feature_cols]
#     X_test = test_encoded[feature_cols]
    
#     # Handle potential column mismatches
#     common_cols = list(set(X_train.columns) & set(X_test.columns))
#     X_train = X_train[common_cols]
#     X_test = X_test[common_cols]
    
#     # Scale features
#     scaler = StandardScaler()
#     X_train_scaled = scaler.fit_transform(X_train)
#     X_test_scaled = scaler.transform(X_test)
    
#     # Prepare target variables
#     y_dict = {}
#     if 'time_diff_seconds' in train_encoded:
#         # Time component targets
#         y_dict['year_diff'] = train_encoded['year_diff']
#         y_dict['month_diff'] = train_encoded['month_diff']
#         y_dict['day_diff'] = train_encoded['day_diff']
#         y_dict['hour_diff'] = train_encoded['hour_diff']
#         y_dict['min_diff'] = train_encoded['min_diff']
#         y_dict['sec_diff'] = train_encoded['sec_diff']
        
#         # Spatial targets
#         y_dict['lat_diff'] = train_encoded['lat_diff']
#         y_dict['lon_diff'] = train_encoded['lon_diff']
#         y_dict['depth_diff'] = train_encoded['depth_diff']
#         y_dict['class_diff'] = train_encoded['class_diff']
    
#     result = {
#         'X_train': X_train,
#         'X_train_scaled': X_train_scaled,
#         'X_test': X_test,
#         'X_test_scaled': X_test_scaled,
#         'train': train,
#         'test': test,
#         'train_encoded': train_encoded,
#         'test_encoded': test_encoded,
#         'feature_cols': feature_cols,
#         'y': y_dict
#     }
    
#     # Optionally create a submission template
#     if create_submission:
#         submission = pd.DataFrame()
#         submission['id_eq'] = test['id_eq']
#         # Add placeholder columns for predictions
#         for col in ['year_as', 'month_as', 'day_as', 'hour_as', 'min_as', 'sec_as',
#                     'lat_as', 'lon_as', 'depth_as', 'class_as']:
#             submission[col] = 0
#         result['submission'] = submission
    
#     return result

In [50]:
nFolds = 7
cv = KFold(n_splits=nFolds, random_state=SEED, shuffle=True)

predictions = {col: np.zeros(len(X_test)) for col in target_cols}

for col in target_cols:
    fold_preds = np.zeros(len(X_test))
    print(f"Training for target: {col}")
    for train_idx, valid_idx in cv.split(X, y):
        X_train, y_train = X.iloc[train_idx].copy(), y.iloc[train_idx][col]
        X_valid, y_valid = X.iloc[valid_idx].copy(), y.iloc[valid_idx][col]
        
        model = lgb.LGBMRegressor(
            n_estimators=number,
            max_depth=-1,
            num_leaves=1024,
            colsample_bytree=0.7,
            learning_rate=0.03,
            objective='regression',
            metric='mae',
            verbosity=-1,  
            device='gpu',  
            random_state=SEED
        )
        
        model.fit(
            X_train, y_train,
            eval_set=[(X_valid, y_valid)],
            eval_metric='mae',
            callbacks=[lgb.early_stopping(stopping_rounds=early_stopping_rounds, verbose=True)]
        )

        
        fold_preds += model.predict(X_test) / nFolds
    predictions[col] = fold_preds

Training for target: year_diff
Training until validation scores don't improve for 100 rounds
Early stopping, best iteration is:
[40]	valid_0's l1: 0.0112598
Training until validation scores don't improve for 100 rounds
Early stopping, best iteration is:
[1]	valid_0's l1: 0.00750946
Training until validation scores don't improve for 100 rounds
Early stopping, best iteration is:
[27]	valid_0's l1: 0.0159126
Training until validation scores don't improve for 100 rounds
Early stopping, best iteration is:
[29]	valid_0's l1: 0.0116598
Training until validation scores don't improve for 100 rounds
Early stopping, best iteration is:
[8]	valid_0's l1: 0.0167449
Training until validation scores don't improve for 100 rounds
Early stopping, best iteration is:
[1]	valid_0's l1: 0.0167674
Training until validation scores don't improve for 100 rounds
Early stopping, best iteration is:
[37]	valid_0's l1: 0.00705724
Training for target: month_diff
Training until validation scores don't improve for 100 r

In [52]:
lgb_preds = predictions

In [53]:
nFolds = 7
cv = KFold(n_splits=nFolds, random_state=SEED, shuffle=True)

predictions = {col: np.zeros(len(X_test)) for col in target_cols}

for col in target_cols:
    fold_preds = np.zeros(len(X_test))
    print(f"Training for target: {col}")
    for train_idx, valid_idx in cv.split(X, y):
        X_train, y_train = X.iloc[train_idx].copy(), y.iloc[train_idx][col]
        X_valid, y_valid = X.iloc[valid_idx].copy(), y.iloc[valid_idx][col]

        
        model = model = xgb.XGBRegressor(
            objective='reg:squarederror',
            eval_metric='mae',
            n_estimators=1500,        
            learning_rate=0.08,
            max_depth=15,
            subsample=1.0,
            colsample_bytree=0.7,
            reg_alpha=0.8,
            reg_lambda=4,
            seed=SEED,                 
            tree_method='gpu_hist',        
            device='gpu' ,
        )


        model.fit(
            X_train, y_train,
            eval_set=[(X_valid, y_valid)],
            verbose = True, 
        )

        fold_preds += np.maximum(model.predict(X_test), 0) / nFolds
    predictions[col] = fold_preds

Training for target: year_diff
[0]	validation_0-mae:0.01194
[1]	validation_0-mae:0.01181
[2]	validation_0-mae:0.01174
[3]	validation_0-mae:0.01170
[4]	validation_0-mae:0.01153
[5]	validation_0-mae:0.01143
[6]	validation_0-mae:0.01135
[7]	validation_0-mae:0.01122
[8]	validation_0-mae:0.01114
[9]	validation_0-mae:0.01109
[10]	validation_0-mae:0.01105
[11]	validation_0-mae:0.01102
[12]	validation_0-mae:0.01092
[13]	validation_0-mae:0.01089
[14]	validation_0-mae:0.01089
[15]	validation_0-mae:0.01076
[16]	validation_0-mae:0.01064
[17]	validation_0-mae:0.01066
[18]	validation_0-mae:0.01071
[19]	validation_0-mae:0.01074
[20]	validation_0-mae:0.01076
[21]	validation_0-mae:0.01075
[22]	validation_0-mae:0.01066
[23]	validation_0-mae:0.01068
[24]	validation_0-mae:0.01072
[25]	validation_0-mae:0.01064
[26]	validation_0-mae:0.01070
[27]	validation_0-mae:0.01064
[28]	validation_0-mae:0.01072
[29]	validation_0-mae:0.01065
[30]	validation_0-mae:0.01059
[31]	validation_0-mae:0.01054
[32]	validation_0-m

In [54]:
xgb_preds = predictions

In [55]:
nFolds = 7
cv = KFold(n_splits=nFolds, random_state=SEED, shuffle=True)

predictions = {col: np.zeros(len(X_test)) for col in target_cols}


for col in target_cols:
    fold_preds = np.zeros(len(X_test))
    print(f"Training for target: {col}")
    
    
    for train_idx, valid_idx in cv.split(X, y):
        X_train, y_train = X.iloc[train_idx].copy(), y.iloc[train_idx][col]
        X_valid, y_valid = X.iloc[valid_idx].copy(), y.iloc[valid_idx][col]
        
        
        model = RandomForestRegressor(
            n_estimators = number,  
            max_depth = 15,  
            min_samples_split = 2, 
            min_samples_leaf = 1,  
            max_features = 1.0,  
            bootstrap = True,
            random_state = SEED,
            n_jobs = -1,  
        )
        model.fit(X_train, y_train)
        
        
        val_pred = model.predict(X_valid)
        score = mean_absolute_error(y_valid, val_pred)
        print(f"Fold MAE: {score}")
        
        fold_preds += np.maximum(model.predict(X_test), 0) / nFolds
    
    predictions[col] = fold_preds


Training for target: year_diff
Fold MAE: 0.015381005586592179
Fold MAE: 0.010024581005586591
Fold MAE: 0.01853631284916201
Fold MAE: 0.012075977653631284
Fold MAE: 0.020395505617977528
Fold MAE: 0.0190438202247191
Fold MAE: 0.009587640449438202
Training for target: month_diff
Fold MAE: 0.2621218201498929
Fold MAE: 0.22943915450535213
Fold MAE: 0.3118521697212942
Fold MAE: 0.2615993508556161
Fold MAE: 0.325688531282219
Fold MAE: 0.3105061206085441
Fold MAE: 0.22364376529363394
Training for target: day_diff
Fold MAE: 3.7626250703968687
Fold MAE: 4.246037501179536
Fold MAE: 3.9591556719748326
Fold MAE: 4.8609005356165085
Fold MAE: 4.327280961792934
Fold MAE: 3.759202399175807
Fold MAE: 4.186707497232556
Training for target: hour_diff
Fold MAE: 5.363905678883068
Fold MAE: 5.931246370283126
Fold MAE: 5.541469597334822
Fold MAE: 5.27035804765897
Fold MAE: 5.362926019406733
Fold MAE: 5.6203029216685945
Fold MAE: 5.433977894149967
Training for target: min_diff
Fold MAE: 19.957507800544334
Fold

In [56]:
rgb_preds = predictions

In [59]:
final_preds = {}
for key in lgb_preds.keys():
    pred_lgb = np.array(lgb_preds[key])
    pred_xgb = np.array(xgb_preds[key])
    pred_rgb = np.array(rgb_preds[key])
    final_preds[key] = 0.4 * pred_lgb + 0.4 * pred_xgb + pred_rgb * 0.2


submission = pd.DataFrame({
    'id_eq': test_df['id_eq'],
    'year_as': test_df['year'] + final_preds['year_diff'],
    'month_as': test_df['month'] + final_preds['month_diff'],
    'day_as': test_df['day'] + final_preds['day_diff'],
    'hour_as': test_df['hour'] + final_preds['hour_diff'],
    'min_as': test_df['min'] + final_preds['min_diff'],
    'sec_as': test_df['sec'] + final_preds['sec_diff'],

    'lat_as': test_df['lat'] + final_preds['lat_diff'],
    'lon_as': test_df['lon'] + final_preds['lon_diff'],
    'depth_as': test_df['depth'] + final_preds['depth_diff'],
    'class_as': test_df['class'] + final_preds['class_diff']
})

submission.to_csv('submission.csv', index=False)
print('Submission file saved as submission.csv')


Submission file saved as submission.csv
